# Create a View of Source Table `[Uploadfile].[CurrentSemesterCourseOfferings]`


In [1]:
-- =============================================
-- Author:		< Daniel Gargiullo, Oksana Weigand-Suminski >
-- Create date: < 12/4/2024 >
-- Description:	< Create View `[Uploadfile].[vw_CurrentSemesterCourseOfferings]` from source table `[Uploadfile].[CurrentSemesterCourseOfferings]`. 
--                ChatGPT 4o assisted >
-- =============================================

USE QueensClassSchedule
GO

CREATE VIEW [Uploadfile].[vw_CurrentSemesterCourseOfferings] AS
SELECT
    [Semester],
    [Sec],
    [Code],
    [Course (hr, crd)] AS OriginalCourseColumn,
    -- Extract CourseName (text before the first '(')
    LTRIM(RTRIM(LEFT([Course (hr, crd)], CHARINDEX('(', [Course (hr, crd)]) - 1))) AS CourseName,
    -- Extract hr (number between '(' and ',')
    LTRIM(RTRIM(SUBSTRING([Course (hr, crd)],
        CHARINDEX('(', [Course (hr, crd)]) + 1,
        CHARINDEX(',', [Course (hr, crd)]) - CHARINDEX('(', [Course (hr, crd)]) - 1))) AS hr,
    -- Extract crd (number between ',' and ')')
    LTRIM(RTRIM(SUBSTRING([Course (hr, crd)],
        CHARINDEX(',', [Course (hr, crd)]) + 1,
        CHARINDEX(')', [Course (hr, crd)]) - CHARINDEX(',', [Course (hr, crd)]) - 1))) AS crd,
    [Description],
    [Day],
    [Time],
    [Instructor],
    [Location],
    [Enrolled],
    [Limit],
    [Mode of Instruction]
FROM
    [Uploadfile].[CurrentSemesterCourseOfferings];


Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.037

# Create the required schemas and User-defined Data Types

### Schemas being created:
- `[Udt]`
- `[DbSecurity]`
- `[Course]`
- `[Location]`
- `[Department]`
- `[Process]`
- `[Project3]`

In [2]:
-- =============================================
-- Author:		< Daniel Gargiullo, Oksana Weigand-Suminski, Jascharan Singh, Sarmad Ali, Augusta Na, Carlos Vega >
-- Create date: < 12/3/2024 >
-- Description:	< Create the required schemas and UDT's >
-- =============================================

USE QueensClassSchedule
GO

CREATE  SCHEMA  [Udt]
GO

CREATE  TYPE    [Udt].[SurrogateKeyInt]     FROM    [int]               NULL
GO
CREATE  TYPE    [Udt].[DateAdded]           FROM    Datetime2(7)    NOT NULL
GO
CREATE  TYPE    [Udt].[ClassTime]           FROM    NCHAR(5)        NOT NULL
GO
CREATE  TYPE    [Udt].[IndividualProject]   FROM    NVARCHAR(60)    NOT NULL
GO
CREATE  TYPE    [Udt].[LastName]            FROM    NVARCHAR(35)    NOT NULL
GO
CREATE  TYPE    [Udt].[FirstName]           FROM    NVARCHAR(20)    NOT NULL
GO
CREATE  TYPE    [Udt].[GroupName]           FROM    NVARCHAR(20)    NOT NULL
GO
CREATE  TYPE    [Udt].[String100]           FROM    NVARCHAR(100)   NOT NULL
GO
CREATE  TYPE    [Udt].[Rows]                FROM    [int]           NOT NULL
GO
CREATE  TYPE    [Udt].[String4]             FROM    NVARCHAR(4)         NULL
GO
CREATE  TYPE    [Udt].[String8]             FROM    NVARCHAR(8)         NULL
GO
CREATE  TYPE    [Udt].[String20]            FROM    NVARCHAR(20)        NULL
GO
CREATE  TYPE    [Udt].[String30]            FROM    NVARCHAR(30)    NOT NULL
GO
CREATE  TYPE    [Udt].[ClassLength]         FROM    NVARCHAR(30)    NOT NULL
GO
CREATE  TYPE    [Udt].[FloatField]          FROM    FLOAT           NOT NULL
GO

-- =============================================
-- Author:		< Daniel Gargiullo, Oksana Weigand-Suminski >
-- Create date: < 12/4/2024 >
-- Description:	< Create the required schemas >
-- =============================================

USE QueensClassSchedule
GO

CREATE  SCHEMA  [DbSecurity]
GO
CREATE  SCHEMA  [Course]
GO
CREATE  SCHEMA  [Location]
GO
CREATE  SCHEMA  [Department]
GO
CREATE  SCHEMA  [Process]
GO

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

...

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.145

# Create `[DbSecurity].[UserAuthorization]` Table

### Create and populate the table storing the group members:

In [3]:
-- =============================================
-- Author:		< Daniel Gargiullo, Oksana Weigand-Suminski >
-- Create date: < 12/4/2024 >
-- Description:	< Create the `[DbSecurity].[UserAuthorization]` table >
-- =============================================

USE QueensClassSchedule
GO

CREATE  TABLE   [DbSecurity].[UserAuthorization]    (
    [UserAuthorizationKey]  [Udt].[SurrogateKeyInt] IDENTITY(1,1)   NOT NULL
        PRIMARY KEY CLUSTERED,
    [ClassTime]             [Udt].[ClassTime]                           NULL    DEFAULT ('10:45'),
    [IndividualProject]     [Udt].[IndividualProject]                   NULL    DEFAULT ('Project 3'),
    [GroupMemberLastName]   [Udt].[LastName]                        NOT NULL,
    [GroupMemberFirstName]  [Udt].[FirstName]                       NOT NULL,
    [GroupName]             [Udt].[GroupName]                       NOT NULL    DEFAULT ('Group 2'),
    [DateAdded]             [Udt].[DateAdded]                           NULL    DEFAULT (SYSDATETIME())
);
GO

INSERT  INTO    [DbSecurity].[UserAuthorization]    (GroupMemberFirstName,   GroupMemberLastName)
VALUES
    ('Sarmad',      'Ali'), 
    ('Daniel',      'Gargiullo'), 
    ('Augusta',     'Na'), 
    ('Jascharan',   'Singh'),
    ('Carlos',      'Vega Lemus'), 
    ('Oksana',      'Weigand-Suminski');

Commands completed successfully.

Commands completed successfully.

(6 rows affected)

Total execution time: 00:00:00.032

# Create Required Tables
- `[Process]`
    - `.[WorkFlowSteps]`
- `[Course]`
    - `.[Course]`
    - `.[Class]`
    - `.[ModeOfInstruction]`
- `[Location]`
    - `.[BuildingLocation]`
    - `.[RoomLocation]`
- `[Department]`
    - `.[Department]`
    - `.[Instructor]`

In [4]:
-- =============================================
-- Author:		< Daniel Gargiullo, Oksana Weigand-Suminski >
-- Create date: < 12/4/2024 >
-- Description:	< Create the other required tables >
-- =============================================

USE QueensClassSchedule
GO

/* [Process] schema */

CREATE  TABLE   [Process].[WorkFlowSteps]   (
    [WorkFlowStepsKey]              [Udt].[SurrogateKeyInt] IDENTITY(1,1)   NOT NULL
        PRIMARY KEY CLUSTERED,
    [WorkFlowStepsDescription]      [Udt].[String100]                       NOT NULL,
    [WorkFlowStepsTableRowCount]    [Udt].[Rows]                                NULL    DEFAULT ((0)),
    [StartingDateTime]              [Udt].[DateAdded]                           NULL    DEFAULT (SYSDATETIME()),
    [EndDateTime]                   [Udt].[DateAdded]                           NULL    DEFAULT (SYSDATETIME()),
    [ClassTime]                     [Udt].[ClassTime]                           NULL    DEFAULT ('10:45'),

    [UserAuthorizationKey]          [Udt].[SurrogateKeyInt]                 NOT NULL
)
GO

/* [Course] schema */

CREATE  TABLE   [Course].[Course]   (
	[CourseID]              [Udt].[SurrogateKeyInt] IDENTITY(1,1)   NOT NULL
        PRIMARY KEY CLUSTERED,
    [Section]               [Udt].[String4]                             NULL,
	[Course]                [Udt].[String30]                            NULL,
    [Semester]              [Udt].[String20]                            NULL,
	[Description]           [Udt].[String100]                           NULL,
    -- Required fields:
	[UserAuthorizationKey]  [Udt].[SurrogateKeyInt]                     NULL,
	[DateAdded]             [Udt].[DateAdded]                           NULL,
	[DateOfLastUpdate]      [Udt].[DateAdded]                           NULL
)
GO

CREATE  TABLE   [Course].[Class]    (
    [ClassID]               [Udt].[SurrogateKeyInt] IDENTITY(1,1)   NOT NULL
        PRIMARY KEY CLUSTERED,
    [Enrollment]            [Udt].[SurrogateKeyInt]                     NULL,
    [Limit]                 [Udt].[SurrogateKeyInt]                     NULL,
    [Section]               [Udt].[String30]                            NULL,
    [Department]            [Udt].[String30]                            NULL,
    [Hours]                 [Udt].[FloatField]                          NULL,
    [Credits]               [Udt].[SurrogateKeyInt]                     NULL,
    [Days]                  [Udt].[String30]                            NULL,
    [ClassStart]            [Udt].[String20]                           NULL,
    [ClassEnd]              [Udt].[String20]                           NULL,
    -- Required fields:
    [UserAuthorizationKey]  [Udt].[SurrogateKeyInt]                     NULL,
    [DateAdded]             [Udt].[DateAdded]                           NULL    DEFAULT (SYSDATETIME()),
    [DateOfLastUpdate]      [Udt].[DateAdded]                           NULL    DEFAULT (SYSDATETIME())
)
GO

CREATE  TABLE   [Course].[ModeOfInstruction]    (
	[ModeID]                [Udt].[SurrogateKeyInt] IDENTITY(1,1)   NOT NULL
        PRIMARY KEY CLUSTERED,
	[ModeName]              [Udt].[String100]                       NOT NULL,
    -- Required fields:
	[UserAuthorizationKey]  [Udt].[SurrogateKeyInt]                     NULL,
	[DateAdded]             [Udt].[DateAdded]                           NULL,
	[DateOfLastUpdate]      [Udt].[DateAdded]                           NULL
);

-- =============================================
-- Author:		< Daniel Gargiullo, Oksana Weigand-Suminski, Carlos Vega >
-- Create date: < 12/5/2024 >
-- Description:	< Create the required tables in the `[Location]` schema >
-- =============================================

/* [Location] schema */

CREATE  TABLE   [Location].[BuildingLocation]   (
    [BuildingLocationID]    [Udt].[SurrogateKeyInt] IDENTITY(1,1)   NOT NULL 
        PRIMARY KEY CLUSTERED,
    [CourseCode]            [Udt].[String30]                        NOT NULL,
    [Description]           [Udt].[String100]                           NULL,
    [Building]              [Udt].[String30]                        NOT NULL,
    [Day]                   [Udt].[String30]                            NULL,
    -- Required fields:
    [UserAuthorizationKey]  [Udt].[SurrogateKeyInt]                     NULL,
    [DateAdded]             [Udt].[DateAdded]                           NULL,
    [DateOfLastUpdate]      [Udt].[DateAdded]                           NULL
)
GO

-- ======================================================================
-- Author:		< Daniel Gargiullo, Oksana Weigand-Suminski >
-- Create date: < 12/5/2024 >
-- Description:	< Create the required tables in the `[Location]` schema >
-- ======================================================================

CREATE  TABLE   [Location].[RoomLocation]   (
	[RoomLocationID]        [Udt].[SurrogateKeyInt] IDENTITY(1,1)   NOT NULL
        PRIMARY KEY CLUSTERED,
    [Room]                  [Udt].[String30]                        NOT NULL,
    [Time]                  [Udt].[String20]                        NOT NULL,
    [Day]                   [Udt].[String20]                        NOT NULL,
	[BuildingLocationID]    [Udt].[SurrogateKeyInt]                 NOT NULL,
    -- Required fields:
	[UserAuthorizationKey]  [Udt].[SurrogateKeyInt]                     NULL,
	[DateAdded]             [Udt].[DateAdded]                           NULL,
	[DateOfLastUpdate]      [Udt].[DateAdded]                           NULL
)
GO

/* [Department] schema */

CREATE  TABLE   [Department].[Department]   (
    [DepartmentID]          [Udt].[SurrogateKeyInt] IDENTITY(1,1)   NOT NULL
        PRIMARY KEY CLUSTERED,
    [InstructorID]          [Udt].[SurrogateKeyInt]                 NOT NULL,
    [DepartmentName]        [Udt].[String8]                         NOT NULL    UNIQUE,
    -- Required fields:
	[UserAuthorizationKey]  [Udt].[SurrogateKeyInt]                     NULL,
	[DateAdded]             [Udt].[DateAdded]                           NULL,
	[DateOfLastUpdate]      [Udt].[DateAdded]                           NULL
)
GO

/***** Possibly implementing this or something similar: *****/
-- Insert department names into the Department table
-- INSERT INTO [Department].[Department] (DepartmentName)
-- SELECT DISTINCT
--     LEFT([Course (hr, crd)], CHARINDEX(' ', [Course (hr, crd)]) - 1)
-- FROM [Uploadfile].[CurrentSemesterCourseOfferings]
-- WHERE [Course (hr, crd)] IS NOT NULL AND CHARINDEX(' ', [Course (hr, crd)]) > 0;
-- GO
/************************************************************/

CREATE  TABLE   [Department].[Instructor]   (
    [InstructorID]          [Udt].[SurrogateKeyInt] IDENTITY(1,1)   NOT NULL
        PRIMARY KEY CLUSTERED,
    [DepartmentID]          [Udt].[SurrogateKeyInt]                 NOT NULL,
    [FirstName]             [Udt].[String30]                        NOT NULL,
    [LastName]              [Udt].[String30]                        NOT NULL,
    -- Required fields:
	[UserAuthorizationKey]  [Udt].[SurrogateKeyInt]                     NULL,
	[DateAdded]             [Udt].[DateAdded]                           NULL,
	[DateOfLastUpdate]      [Udt].[DateAdded]                           NULL
)
GO

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.075

# Create Workflow Procedures

- `[Process]`
    - `[usp_TrackWorkFlow]`
    - `[usp_ShowWorkFlowSteps]`

In [5]:
-- =============================================
-- Author:		< Daniel Gargiullo, Oksana Weigand-Suminski >
-- Create date: < 12/5/2024 >
-- Description:	< Create `[Process].[usp_TrackWorkFlow]` and `[Process].[usp_ShowWorkFlowSteps]` procedures >
-- =============================================

USE QueensClassSchedule
GO

CREATE PROCEDURE [Process].[usp_TrackWorkFlow]
    @UserAuthorizationKey INT,
    @WorkFlowStepsTableRowCount INT,
    @WorkFlowStepsDescription NVARCHAR(100)
AS
BEGIN
    INSERT INTO [Process].[WorkFlowSteps]
        (UserAuthorizationKey, WorkFlowStepsTableRowCount, WorkFlowStepsDescription)
    VALUES(@UserAuthorizationKey, @WorkFlowStepsTableRowCount, @WorkFlowStepsDescription);
END;
GO

CREATE PROCEDURE [Process].[usp_ShowWorkFlowSteps] 
AS
BEGIN
	SELECT *
	FROM [Process].[WorkFlowSteps];
END;
GO

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.016

In [6]:
-- ================================================================
-- Author:		< Daniel Gargiullo, Oksana Weigand-Suminski >
-- Create date: < 12/6/2024 >
-- Description:	< Create the `[Process].[usp_TrackWorkFlowSteps]` >
-- ================================================================

USE QueensClassSchedule
GO

CREATE PROCEDURE [Course].[usp_LoadClassTable]
@UserAuthorizationKey INT
AS
BEGIN
    INSERT INTO [Course].[Class] (
        Section,
        Department,
        Hours,
        Credits,
        Days,
        ClassStart,
        ClassEnd,
        Enrollment,
        [Limit],
        UserAuthorizationKey,
        DateAdded,
        DateOfLastUpdate
    )
    SELECT
        [Sec] AS Section,
        LEFT([Course (hr, crd)], CHARINDEX(' ', [Course (hr, crd)]) - 1) AS Department,
        TRY_CAST(
            TRIM(
                SUBSTRING(
                    [Course (hr, crd)],
                    CHARINDEX('(', [Course (hr, crd)]) + 1,
                    CHARINDEX(',', [Course (hr, crd)]) - CHARINDEX('(', [Course (hr, crd)]) - 1
                )
            ) AS FLOAT
        ) AS Hours,
        TRY_CAST(
            TRIM(
                SUBSTRING(
                    [Course (hr, crd)],
                    CHARINDEX(',', [Course (hr, crd)]) + 1,
                    CHARINDEX(')', [Course (hr, crd)]) - CHARINDEX(',', [Course (hr, crd)]) - 1
                )
            ) AS INT
        ) AS Credits,
        [Day] AS Days,
        TRIM(LEFT([Time], CHARINDEX('-', [Time]) - 1)) AS ClassStart,
        TRIM(SUBSTRING([Time], CHARINDEX('-', [Time]) + 1, LEN([Time]))) AS ClassEnd,
        TRY_CAST([Enrolled] AS INT) AS Enrollment,
        TRY_CAST([Limit] AS INT) AS [Limit],
        @UserAuthorizationKey,
        SYSDATETIME() AS DateAdded,
        SYSDATETIME() AS DateOfLastUpdate
    FROM [Uploadfile].[CurrentSemesterCourseOfferings] c
    WHERE
        [Course (hr, crd)] IS NOT NULL
        AND CHARINDEX(' ', [Course (hr, crd)]) > 0
        AND CHARINDEX('-', [Time]) > 0;

    EXEC [Process].[usp_TrackWorkFlow] 
        @UserAuthorizationKey = @UserAuthorizationKey,
        @WorkFlowStepsDescription = 'Loading data into Class table',
        @WorkFlowStepsTableRowCount = @@ROWCOUNT;
END;
GO

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.012

In [7]:
USE QueensClassSchedule 
GO 

EXEC [Course].[usp_LoadClassTable] @UserAuthorizationKey = 6
GO

EXEC [Course].[usp_LoadClassTable] @UserAuthorizationKey = 2
GO

Commands completed successfully.

(4522 rows affected)

(1 row affected)

(4522 rows affected)

(1 row affected)

Total execution time: 00:00:00.238

In [8]:
-- ================================================================
-- Author:		< Daniel Gargiullo, Oksana Weigand-Suminski >
-- Create date: < 12/6/2024 >
-- Description:	< Create the `[Process].[usp_TrackWorkFlowSteps]` >
-- ================================================================

USE QueensClassSchedule
GO

CREATE OR ALTER PROCEDURE [Course].[usp_LoadModeOfInstructionTable]
    @UserAuthorizationKey INT
AS
BEGIN
    -- Insert into the customer table including the user auth key
    INSERT INTO Course.ModeOfInstruction
    (
        ModeName,
        UserAuthorizationKey,
        DateAdded,
        DateOfLastUpdate
    )
    SELECT [Mode of Instruction] AS ModeName, @UserAuthorizationKey, SYSDATETIME() AS DateAdded, SYSDATETIME() AS DateOfLastUpdate
    FROM Uploadfile.CurrentSemesterCourseOfferings

    SELECT * from Course.ModeOfInstruction

    --  Insert the user into the Process.WorkFlowTable
    EXEC [Process].[usp_TrackWorkFlow] @UserAuthorizationKey = @UserAuthorizationKey, @WorkFlowStepsDescription =  'Loading data into MOI table',
    @WorkFlowStepsTableRowCount = @@ROWCOUNT;
END
GO

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.012

In [9]:
USE QueensClassSchedule
GO

EXEC [Course].[usp_LoadModeOfInstructionTable] @UserAuthorizationKey = 2
GO

EXEC [Course].[usp_LoadModeOfInstructionTable] @UserAuthorizationKey = 6
GO

Commands completed successfully.

(4522 rows affected)

(4522 rows affected)

(1 row affected)

(4522 rows affected)

...

(1 row affected)

Displaying Top 5000 rows.

Total execution time: 00:00:00.591

ModeID ModeName UserAuthorizationKey DateAdded DateOfLastUpdate 1 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 2 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 3 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 4 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 5 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 6 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 7 Hybrid 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 8 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 9 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 10 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 11 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 12 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 13 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 14 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 15 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 16 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 17 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 18 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 19 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 20 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 21 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 22 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 23 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 24 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 25 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 26 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 27 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 28 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 29 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 30 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 31 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 32 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 33 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 34 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 35 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 36 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 37 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 38 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 39 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 40 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 41 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 42 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 43 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 44 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 45 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 46 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 47 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 48 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 49 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 50 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 51 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 52 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 53 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 54 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 55 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 56 Online 2 2024-12-07 02:37:36.5070470 202

ModeID ModeName UserAuthorizationKey DateAdded DateOfLastUpdate 1 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 2 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 3 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 4 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 5 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 6 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 7 Hybrid 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 8 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 9 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 10 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 11 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 12 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 13 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 14 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 15 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 16 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 17 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 18 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 19 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 20 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 21 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 22 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 23 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 24 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 25 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 26 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 27 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 28 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 29 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 30 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 31 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 32 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 33 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 34 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 35 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 36 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 37 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 38 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 39 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 40 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 41 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 42 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 43 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 44 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 45 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 46 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 47 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 48 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 49 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 50 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 51 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 52 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 53 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 54 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 55 In-Person 2 2024-12-07 02:37:36.5070470 2024-12-07 02:37:36.5070470 56 Online 2 2024-12-07 02:37:36.5070470 202

# Course.Course Procedure

In [10]:
-- =============================================================
-- Author:		< Daniel Gargiullo, Oksana Weigand-Suminski >
-- Create date: < 12/6/2024 >
-- Description:	< Create the `[Course].[usp_LoadCourseTable]` >
-- =============================================================

USE QueensClassSchedule 
GO 

CREATE OR ALTER PROCEDURE [Course].[usp_LoadCourseTable]
    @UserAuthorizationKey INT
AS
BEGIN

    INSERT INTO Course.Course
    (
        Section, 
        Course, 
        [Semester], 
        [Description], 
        UserAuthorizationKey,
        DateAdded,
        DateOfLastUpdate
    )
    SELECT DISTINCT
        [Sec] AS Section, 
        SUBSTRING([Course (hr, crd)], 1, CHARINDEX('(', [Course (hr, crd)]) - 1) AS Course,
        [Semester],
        [Description],
        @UserAuthorizationKey,
        SYSDATETIME() AS DateAdded, 
        SYSDATETIME() AS DateOfLastUpdate
    FROM Uploadfile.CurrentSemesterCourseOfferings;

    SELECT TOP 50 * 
    FROM Course.Course;

    -- Log the workflow step
    EXEC [Process].[usp_TrackWorkFlow] 
        @UserAuthorizationKey = @UserAuthorizationKey, 
        @WorkflowStepsDescription = 'Loading data into Course table',
        @WorkflowStepsTableRowCount = @@ROWCOUNT;
END;
GO


Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.059

In [11]:
USE QueensClassSchedule
GO

EXEC [Course].[usp_LoadCourseTable] @UserAuthorizationKey = 6
GO

EXEC [Course].[usp_LoadCourseTable] @UserAuthorizationKey = 2
GO

Commands completed successfully.

(4187 rows affected)

(50 rows affected)

(1 row affected)

(4187 rows affected)

(50 rows affected)

(1 row affected)

Total execution time: 00:00:00.356

CourseID Section Course Semester Description UserAuthorizationKey DateAdded DateOfLastUpdate 1 01 ACCT 100 Current Semester Fin & Mgr Acct 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 2 01 ACCT 101 Current Semester Int Theo & Prac Acct 1 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 3 01 ACCT 102 Current Semester Intro Theo & Prac Acct 2 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 4 01 ACCT 201 Current Semester Inter Acct 1 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 5 01 ACCT 202 Current Semester Inter Acct 2 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 6 01 ACCT 261 Current Semester Business Law l 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 7 01 ACCT 305 Current Semester Cost Acct 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 8 01 ACCT 306 Current Semester Quant Techniq Pln & Ctrl 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 9 01 ACCT 311 Current Semester Advcd Acct 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 10 01 ACCT 321 Current Semester Auditing 1 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 11 01 ACCT 322 Current Semester Auditing 2 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 12 01 ACCT 341 Current Semester Acct Info Syst 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 13 01 ACCT 343 Current Semester Microcomp Apps Acct 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 14 01 ACCT 350 Current Semester Finan Stat Analys 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 15 01 ACCT 362 Current Semester Business Law 2 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 16 01 ACCT 362W Current Semester Business Law 2 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 17 01 ACCT 363 Current Semester Business Law 3 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 18 01 ACCT 367 Current Semester Fed & Ny State Tax 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 19 01 ACCT 372 Current Semester Gov & Nfp Acct & Aud 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 20 01 ACCT 393W Current Semester Seminar in Accounting 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 21 01 ACCT 398 Current Semester Internship 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 22 01 ACCT 707 Current Semester Issues In Mgmt Acct 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 23 01 ACCT 712 Current Semester Adv Fin Acct Theory 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 24 01 ACCT 723 Current Semester Adv Auditing Theory 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 25 01 ACCT 747 Current Semester Comm & Accountants 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 26 01 ACCT 748 Current Semester Adv Acct Info Systms 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 27 01 ACCT 752 Current Semester Adv Stdy In Bus Law 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 28 01 ACCT 757 Current Semester Taxation Of Bus Ents 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 29 01 ACCT 758 Current Semester State & Local Taxatn 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 30 01 ACCT 773 Current Semester Govt Acct & Audit 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 31 01 AFST 102 Current Semester Survey African Civ 2 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 32 01 AFST 201W Current Semester Intro Black Cultures 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 33 01 AFST 234W Current Semester Black Women Writers 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 34 01 AFST 300W Current Semester Africana Studies Sem 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 35 01 AMST 110W Current Semester Intro Amer Soc/Culture 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 36 01 ANTH 101 Current Semester Intro To Cultural Anthropology 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 37 01 ANTH

CourseID Section Course Semester Description UserAuthorizationKey DateAdded DateOfLastUpdate 1 01 ACCT 100 Current Semester Fin & Mgr Acct 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 2 01 ACCT 101 Current Semester Int Theo & Prac Acct 1 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 3 01 ACCT 102 Current Semester Intro Theo & Prac Acct 2 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 4 01 ACCT 201 Current Semester Inter Acct 1 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 5 01 ACCT 202 Current Semester Inter Acct 2 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 6 01 ACCT 261 Current Semester Business Law l 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 7 01 ACCT 305 Current Semester Cost Acct 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 8 01 ACCT 306 Current Semester Quant Techniq Pln & Ctrl 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 9 01 ACCT 311 Current Semester Advcd Acct 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 10 01 ACCT 321 Current Semester Auditing 1 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 11 01 ACCT 322 Current Semester Auditing 2 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 12 01 ACCT 341 Current Semester Acct Info Syst 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 13 01 ACCT 343 Current Semester Microcomp Apps Acct 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 14 01 ACCT 350 Current Semester Finan Stat Analys 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 15 01 ACCT 362 Current Semester Business Law 2 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 16 01 ACCT 362W Current Semester Business Law 2 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 17 01 ACCT 363 Current Semester Business Law 3 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 18 01 ACCT 367 Current Semester Fed & Ny State Tax 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 19 01 ACCT 372 Current Semester Gov & Nfp Acct & Aud 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 20 01 ACCT 393W Current Semester Seminar in Accounting 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 21 01 ACCT 398 Current Semester Internship 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 22 01 ACCT 707 Current Semester Issues In Mgmt Acct 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 23 01 ACCT 712 Current Semester Adv Fin Acct Theory 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 24 01 ACCT 723 Current Semester Adv Auditing Theory 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 25 01 ACCT 747 Current Semester Comm & Accountants 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 26 01 ACCT 748 Current Semester Adv Acct Info Systms 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 27 01 ACCT 752 Current Semester Adv Stdy In Bus Law 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 28 01 ACCT 757 Current Semester Taxation Of Bus Ents 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 29 01 ACCT 758 Current Semester State & Local Taxatn 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 30 01 ACCT 773 Current Semester Govt Acct & Audit 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 31 01 AFST 102 Current Semester Survey African Civ 2 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 32 01 AFST 201W Current Semester Intro Black Cultures 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 33 01 AFST 234W Current Semester Black Women Writers 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 34 01 AFST 300W Current Semester Africana Studies Sem 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 35 01 AMST 110W Current Semester Intro Amer Soc/Culture 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 36 01 ANTH 101 Current Semester Intro To Cultural Anthropology 6 2024-12-07 02:37:40.4073145 2024-12-07 02:37:40.4073145 37 01 ANTH